# Исследовательский анализ данных

In [1]:
import numpy as np
import math
import requests
import folium
from folium.plugins import TimestampedGeoJson
from geopy.distance import geodesic
from datetime import datetime, timedelta
from shapely.geometry import LineString, shape, Point, Polygon
from pyproj import Transformer


## Предобработка данных

Загружаем и распаковываем данные, которые мы получили из API.

In [2]:
# Запрос к серверу для получения данных последней миссии
response = requests.get("http://localhost:5005/get-mission")
mission_data = response.json()

drone_data = mission_data.get('droneData', {})
route_points = mission_data.get('routePoints', [])
saved_polygons = mission_data.get('savedPolygons', {})

print(drone_data)
print(route_points)
print(saved_polygons)

{'altitude': 0, 'lat': 55.139592, 'lng': 37.962471}
[{'altitude': 33, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.140416152657565, 'lng': 37.9639683191827}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14083798992547, 'lng': 37.965575093921274}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.141591309391515, 'lng': 37.96682878836921}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.1417582822599, 'lng': 37.96613687580222}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14138039529615, 'lng': 37.964430158136906}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14147267076268, 'lng': 37.96302367278898}, {'altitude': 33, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.141499035024594, 'lng': 37.96203193144294}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.141213421259664, 'lng': 37.9612247001148}, {'altitude': 330, 'flightAltitude'

Наносим на карту

In [3]:
# Создаём карту
m = folium.Map(location=[drone_data.get('lat', 0), drone_data.get('lng', 0)], zoom_start=16)

# Добавляем маркер дрона красного цвета
folium.Marker(
    [drone_data.get('lat', 0), drone_data.get('lng', 0)],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Добавляем маршрутные точки
for pt in route_points:
    folium.Marker(
        [pt.get('lat', 0), pt.get('lng', 0)],
        popup=f"Информация: {pt.get('lat', 'нет данных'), pt.get('lng', 'нет данных'), pt.get('altitude', 'нет данных')}",
        icon=folium.Icon(color='blue', icon='cloud')  # Можно выбрать любой цвет и иконку
    ).add_to(m)

# Соединяем маршрутные точки пунктирной линией
if len(route_points) > 1:
    folium.PolyLine(
        locations=[(pt.get('lat', 0), pt.get('lng', 0)) for pt in route_points],
        color='blue',
        weight=3,
        opacity=0.7,
        dash_array="5, 5" # пунктир
    ).add_to(m)


# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)



# Добавляем полигоны
if saved_polygons and saved_polygons.get('features'):
    folium.GeoJson(saved_polygons).add_to(m)

# Отображаем карту
m

In [4]:
# # Создаем объект Polygon из первого элемента saved_polygons
#
# polygon_wgs = shape(saved_polygons["features"][0]["geometry"])
# # Проверяем, что тип объекта - Polygon
# assert polygon_wgs.geom_type == 'Polygon'

Преобразуем маршрутные точки в LineString и генерируем новые с шагом 1м

In [5]:
# Преобразование координат: из WGS84 в UTM
# Для Москвы часто используют UTM zone 37N (EPSG:32637), проверьте корректность для вашей области.
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

# Преобразуем координаты маршрутных точек в UTM
route_coords_m = []
for pt in route_points:
    x, y = transformer_to_m.transform(pt["lng"], pt["lat"])
    route_coords_m.append((x, y))

# Создаем LineString в метрической системе
route_line = LineString(route_coords_m)

# Генерируем новые точки на маршруте с шагом 1 метр
step = 1.0
points_along_route = []
distance = 0.0

while distance <= route_line.length:
    pt = route_line.interpolate(distance)
    points_along_route.append(pt)
    distance += step


In [6]:
# Преобразуем полигон в UTM (для корректных расчетов)
def transform_polygon_to_utm(polygon_wgs, transformer):
    # Получаем координаты полигона, преобразуем каждую точку
    utm_coords = []
    for ring in polygon_wgs.exterior.coords:
        x, y = transformer.transform(ring[0], ring[1])
        utm_coords.append((x, y))
    return Polygon(utm_coords)

# polygon_utm = transform_polygon_to_utm(polygon_wgs, transformer_to_m)

In [7]:
# Преобразуем каждый полигон из saved_polygons в объект Shapely и затем в UTM
polygons_utm = []
for feature in saved_polygons["features"]:
    poly_wgs = shape(feature["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
    polygons_utm.append(poly_utm)

In [8]:
# Функция для вычисления проекции точки на отрезок (ребро)
def point_to_segment_projection(point, seg_start, seg_end):
    """
    point, seg_start, seg_end - кортежи (x, y)
    Возвращает: (projection, distance)
    projection: координаты проекции (x, y)
    distance: расстояние от точки до проекции
    """
    p = np.array(point)
    a = np.array(seg_start)
    b = np.array(seg_end)
    ab = b - a
    if np.allclose(ab, 0):
        return a, np.linalg.norm(p - a)
    t = np.dot(p - a, ab) / np.dot(ab, ab)
    if t < 0:
        projection = a
    elif t > 1:
        projection = b
    else:
        projection = a + t * ab
    distance = np.linalg.norm(p - projection)
    return projection, distance


In [9]:
# Функция для получения ближайшей проекции (перпендикуляра) от точки к границе полигона
def get_nearest_projection_on_polygon(point, polygon):
    """
    point: shapely Point (в UTM)
    polygon: shapely Polygon (в UTM)
    Возвращает: (projection, distance), где projection - кортеж (x, y)
    """
    coords = list(polygon.exterior.coords)
    min_distance = float('inf')
    best_proj = None
    # Проходим по каждому ребру полигона
    for i in range(len(coords) - 1):  # последний элемент равен первому
        a = coords[i]
        b = coords[i+1]
        proj, dist = point_to_segment_projection((point.x, point.y), a, b)
        if dist < min_distance:
            min_distance = dist
            best_proj = proj
    return best_proj, min_distance

In [10]:
# Функция для перебора всех полигонов и выбора проекции с минимальным расстоянием
def get_nearest_projection(point, polygons):
    overall_best_proj = None
    overall_min_dist = float('inf')
    for poly in polygons:
        proj, dist = get_nearest_projection_on_polygon(point, poly)
        if dist < overall_min_dist:
            overall_min_dist = dist
            overall_best_proj = proj
    return overall_best_proj, overall_min_dist

In [11]:
# Для каждой сгенерированной точки вдоль маршрута находим проекцию на ближайшее ребро полигона
projections = []
for pt in points_along_route:
    best_proj, d = get_nearest_projection(pt, polygons_utm)
    projections.append((pt, Point(best_proj)))

In [12]:
# Преобразуем точки и проекции обратно в WGS84 для отображения
points_along_route_wgs = []
projections_wgs = []
for pt, proj_pt in projections:
    lng_pt, lat_pt = transformer_to_wgs.transform(pt.x, pt.y)
    lng_proj, lat_proj = transformer_to_wgs.transform(proj_pt.x, proj_pt.y)
    points_along_route_wgs.append((lat_pt, lng_pt))
    projections_wgs.append((lat_proj, lng_proj))

In [13]:
# Отрисовка на карте с помощью Folium
m = folium.Map(location=[drone_data["lat"], drone_data["lng"]], zoom_start=16)

# Маркер дрона (красный)
folium.Marker(
    [drone_data["lat"], drone_data["lng"]],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Отобразим сгенерированные точки маршрута (синие кружки)
for pt in points_along_route_wgs:
    folium.CircleMarker(
        location=pt,
        radius=1,
        color='blue',
        fill=True,
        fill_color='blue'
    ).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Соединяем последовательные маршрутные точки (пунктирной линией)
folium.PolyLine(
    locations=[(pt["lat"], pt["lng"]) for pt in route_points],
    color="blue",
    weight=3,
    opacity=0.7,
    dash_array="5, 5"
).add_to(m)

# Отображаем полигоны через GeoJson
folium.GeoJson(saved_polygons).add_to(m)

# Отображаем линии-перпендикуляры (зеленые) для каждой точки
for pt, proj_pt in zip(points_along_route_wgs, projections_wgs):
    folium.PolyLine(
        locations=[pt, proj_pt],
        color="green",
        weight=1,
        opacity=0.8,
        dash_array="2, 4"
    ).add_to(m)

m

Отступаем произвольное число в метрах от точки соприкосновения каждого полигона с высотами на самой проекции

In [14]:
offset_distance = 3.0  # отступ в метрах

# Предполагаем, что projections имеет формат: [(pt, proj_pt), ...]
# где pt – исходная точка (shapely.Point) вдоль маршрута (в UTM),
# а proj_pt – проекция этой точки на полигон (также shapely.Point, в UTM)

corrected_projections = []
for pt, proj_pt in projections:
    # Вычисляем вектор от проекции к исходной точке
    v = np.array([pt.x - proj_pt.x, pt.y - proj_pt.y])
    norm_v = np.linalg.norm(v)
    if norm_v == 0:
        # Если вектор нулевой, оставляем проекцию без смещения
        corrected_point = proj_pt
    else:
        unit_v = v / norm_v
        corrected_coords = np.array([proj_pt.x, proj_pt.y]) + offset_distance * unit_v
        corrected_point = Point(corrected_coords)
    corrected_projections.append(corrected_point)

In [15]:
corrected_points_wgs = []
for cp in corrected_projections:
    lng, lat = transformer_to_wgs.transform(cp.x, cp.y)
    corrected_points_wgs.append((lat, lng))

In [16]:
# Создаем карту
m = folium.Map(location=[drone_data["lat"], drone_data["lng"]], zoom_start=16)

# Отрисовываем полигоны
if saved_polygons and saved_polygons.get('features'):
    folium.GeoJson(saved_polygons, style_function=lambda x: {
        'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3
    }).add_to(m)

# Добавляем маркер дрона
folium.Marker(
    [drone_data["lat"], drone_data["lng"]],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Отрисовываем исходный маршрут (например, пунктирной линией) по исходным точкам
folium.PolyLine(
    locations=[(pt["lat"], pt["lng"]) for pt in route_points],
    color="blue",
    weight=3,
    opacity=0.7,
    dash_array="5,5"
).add_to(m)

# Отображаем смещённые точки скорректированного маршрута (зелёные кружки)
for pt in corrected_points_wgs:
    folium.CircleMarker(
        location=pt,
        radius=2,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(m)

# Соединяем смещённые точки линией (скорректированная миссия)
folium.PolyLine(
    locations=corrected_points_wgs,
    color="green",
    weight=3,
    opacity=0.8
).add_to(m)

m

## Проработка алгоритма огибания пересекаемых участков полигонов

### Реализация деления на участки, которые пересекают полигон и не пересекают

In [17]:
# Функция для преобразования (lng, lat) в (lat, lng) для Folium
def to_latlon(coord):
    return (coord[1], coord[0])

# Формируем исходный маршрут (shapely LineString, координаты: (lng, lat))
route_line = LineString([(pt['lng'], pt['lat']) for pt in route_points])
route_coords = list(route_line.coords)

# Функция для корректировки одного сегмента маршрута, если он пересекает полигон
def correct_segment(segment, poly):
    """
    segment: LineString (два узловых точки)
    polygons: список объектов Polygon
    Если сегмент пересекается с каким-либо полигоном, возвращает скорректированный LineString,
    иначе возвращает исходный segment.
    """
    for poly in polygons:
        if segment.intersects(poly):
            # Вычисляем пересечение
            intersection = segment.intersection(poly)
            if intersection.is_empty:
                continue
            # Определяем точки входа и выхода для этого сегмента:
            if intersection.geom_type == 'LineString':
                entry = Point(intersection.coords[0])
                exit = Point(intersection.coords[-1])
            elif intersection.geom_type == 'MultiLineString':
                merged = linemerge(intersection)
                if merged.geom_type == 'LineString':
                    entry = Point(merged.coords[0])
                    exit = Point(merged.coords[-1])
                else:
                    pts = []
                    for ls in merged.geoms:
                        pts.extend(list(ls.coords))
                    entry = Point(min(pts, key=lambda c: segment.project(Point(c))))
                    exit = Point(max(pts, key=lambda c: segment.project(Point(c))))
            elif intersection.geom_type == 'MultiPoint':
                pts = list(intersection)
                entry, exit = pts[0], pts[-1]
            else:
                continue

            # Получаем границу полигона
            boundary = poly.exterior
            entry_dist = boundary.project(entry)
            exit_dist = boundary.project(exit)
            if entry_dist > exit_dist:
                entry_dist, exit_dist = exit_dist, entry_dist

            # Кандидат 1: обход от точки входа до точки выхода по границе
            candidate1_coords = [boundary.interpolate(d).coords[0] for d in np.linspace(entry_dist, exit_dist, num=20)]
            candidate1_line = LineString(candidate1_coords)
            total_length = boundary.length
            # Кандидат 2: обход в обратную сторону (через остаток границы)
            candidate2_coords = [boundary.interpolate(d % total_length).coords[0]
                                 for d in np.linspace(entry_dist, entry_dist + total_length - (exit_dist - entry_dist), num=20)]
            candidate2_line = LineString(candidate2_coords)
            bypass = candidate1_line if candidate1_line.length < candidate2_line.length else candidate2_line

            # Формируем скорректированный сегмент:
            # От начала сегмента до точки входа, затем обходной сегмент, затем от точки выхода до конца сегмента.
            seg_coords = list(segment.coords)
            # Находим ближайшие индексы для точек входа и выхода в сегменте
            def find_nearest_index(coords, pt):
                dists = [Point(coord).distance(pt) for coord in coords]
                return np.argmin(dists)
            entry_index = find_nearest_index(seg_coords, entry)
            exit_index = find_nearest_index(seg_coords, exit)
            if entry_index > exit_index:
                entry_index, exit_index = exit_index, entry_index
            new_seg_coords = seg_coords[:entry_index+1] + list(bypass.coords) + seg_coords[exit_index:]
            return LineString(new_seg_coords)
    return segment  # если пересечений нет

# Преобразуем список сохранённых полигонов в объекты shapely Polygon
polygons = [Polygon(feature['geometry']['coordinates'][0]) for feature in saved_polygons['features']]

# Разбиваем исходный маршрут на сегменты (каждый отрезок между двумя соседними точками)
segments = []
for i in range(len(route_coords) - 1):
    seg = LineString([route_coords[i], route_coords[i+1]])
    segments.append(seg)

# Обрабатываем каждый сегмент:
corrected_segments = []
for seg in segments:
    corrected_seg = correct_segment(seg, polygons)
    corrected_segments.append(corrected_seg)

# Объединяем скорректированные сегменты в один маршрут
corrected_coords = []
for seg in corrected_segments:
    coords = list(seg.coords)
    if corrected_coords and coords[0] == corrected_coords[-1]:
        corrected_coords.extend(coords[1:])
    else:
        corrected_coords.extend(coords)
corrected_route = LineString(corrected_coords)


In [18]:
# --- Отрисовка на карте с Folium ---
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем исходный маршрут (синяя пунктирная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue',
    weight=3,
    opacity=0.7,
    dash_array='5,5'
).add_to(m)

# Отображаем скорректированный маршрут (зелёная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in corrected_route.coords],
    color='green',
    weight=3,
    opacity=0.8
).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

m

In [19]:
import folium
import numpy as np
from shapely.geometry import LineString, Polygon, Point
from shapely.ops import linemerge

# Функция для преобразования координат (lng, lat) -> (lat, lng) для Folium
def to_latlon(coord):
    return (coord[1], coord[0])

# Функция для разрезания линии (LineString) на две части в заданном расстоянии
def cut(line, distance):
    """
    Разрезает LineString line на две части в точке, находящейся на расстоянии distance от начала.
    Возвращает список из двух LineString.
    Если distance вне диапазона, возвращает оригинальный line в одном элементе списка.
    """
    if distance <= 0.0 or distance >= line.length:
        return [LineString(line.coords)]
    coords = list(line.coords)
    for i, p in enumerate(coords):
        pd = line.project(Point(p))
        if np.isclose(pd, distance):
            return [
                LineString(coords[:i+1]),
                LineString(coords[i:])
            ]
        if pd > distance:
            cp = line.interpolate(distance)
            return [
                LineString(coords[:i] + [(cp.x, cp.y)]),
                LineString([(cp.x, cp.y)] + coords[i:])
            ]

# Функция для объединения нескольких LineString по их координатам
def merge_lines(lines):
    merged_coords = []
    for line in lines:
        coords = list(line.coords)
        if merged_coords and np.allclose(coords[0], merged_coords[-1]):
            merged_coords.extend(coords[1:])
        else:
            merged_coords.extend(coords)
    return LineString(merged_coords)

# Функция для корректировки одного сегмента маршрута, заменяя лишь часть, которая проходит через полигон
def refined_correct_segment(segment, poly):
    """
    Если сегмент пересекается с полигоном, вычисляет расстояния вдоль segment, где начинается и заканчивается пересечение.
    Затем разрезает segment на safe части (до входа и после выхода) и заменяет внутреннюю часть обходным сегментом,
    вычисляемым вдоль границы полигона между проекциями этих точек.
    Если сегмент не пересекается с poly – возвращает segment без изменений.
    """
    if not segment.intersects(poly):
        return segment

    # Вычисляем пересечение сегмента с полигоном
    intersection = segment.intersection(poly)
    if intersection.is_empty:
        return segment

    # Обработка типов пересечения: предпочитаем LineString или объединяем MultiLineString
    if intersection.geom_type == 'LineString':
        entry = Point(intersection.coords[0])
        exit = Point(intersection.coords[-1])
    elif intersection.geom_type == 'MultiLineString':
        merged = linemerge(intersection)
        if merged.geom_type == 'LineString':
            entry = Point(merged.coords[0])
            exit = Point(merged.coords[-1])
        else:
            pts = []
            for ls in merged.geoms:
                pts.extend(list(ls.coords))
            entry = Point(min(pts, key=lambda c: segment.project(Point(c))))
            exit = Point(max(pts, key=lambda c: segment.project(Point(c))))
    elif intersection.geom_type == 'MultiPoint':
        pts = list(intersection)
        entry, exit = pts[0], pts[-1]
    else:
        # Если тип пересечения не предвиден, ничего не меняем
        return segment

    # Определяем расстояния вдоль сегмента для точек входа и выхода
    d_entry = segment.project(entry)
    d_exit = segment.project(exit)
    if d_entry > d_exit:
        d_entry, d_exit = d_exit, d_entry

    # Разрезаем сегмент на три части
    parts = []
    if d_entry > 0:
        parts.append(cut(segment, d_entry)[0])
    # Центральная часть, которую заменим – от d_entry до d_exit
    central_parts = cut(segment, d_entry)
    if len(central_parts) == 2:
        central_part = central_parts[1]
        central_parts = cut(central_part, d_exit - d_entry)
        if len(central_parts) == 2:
            central_inside = central_parts[0]
        else:
            central_inside = central_part
    else:
        central_inside = segment
    if d_exit < segment.length:
        parts.append(cut(segment, d_exit)[1])

    # Теперь вычисляем обходной сегмент вдоль границы полигона между проекциями точек entry и exit.
    # Находим проекции entry и exit на границу полигона.
    boundary = poly.exterior
    proj_entry = Point(boundary.interpolate(boundary.project(entry)).coords[0])
    proj_exit  = Point(boundary.interpolate(boundary.project(exit)).coords[0])
    # Вычисляем расстояния вдоль границы
    b_entry = boundary.project(proj_entry)
    b_exit  = boundary.project(proj_exit)
    if b_entry > b_exit:
        b_entry, b_exit = b_exit, b_entry

    candidate1_coords = [boundary.interpolate(d).coords[0] for d in np.linspace(b_entry, b_exit, num=20)]
    candidate1_line = LineString(candidate1_coords)
    total_length = boundary.length
    candidate2_coords = [boundary.interpolate(d % total_length).coords[0] for d in np.linspace(b_entry, b_entry + total_length - (b_exit - b_entry), num=20)]
    candidate2_line = LineString(candidate2_coords)
    bypass = candidate1_line if candidate1_line.length < candidate2_line.length else candidate2_line

    # Формируем новый сегмент: безопасная часть до d_entry, затем обходной сегмент, затем безопасная часть после d_exit.
    safe_before = cut(segment, d_entry)[0] if d_entry > 0 else None
    safe_after = cut(segment, d_exit)[1] if d_exit < segment.length else None

    new_coords = []
    if safe_before is not None:
        new_coords.extend(list(safe_before.coords))
    new_coords.extend(list(bypass.coords))
    if safe_after is not None:
        # Избегаем дублирования последней координаты обхода
        new_coords.extend(list(safe_after.coords)[1:])
    return LineString(new_coords)

# Итеративная корректировка маршрута для всех сегментов и для всех полигонов
def refine_route_for_polygons(route_line, polygons):
    route_coords = list(route_line.coords)
    # Разбиваем исходный маршрут на сегменты между соседними точками
    segments = [LineString([route_coords[i], route_coords[i+1]]) for i in range(len(route_coords)-1)]
    corrected_segments = []
    for seg in segments:
        corrected_seg = seg
        for poly in polygons:
            corrected_seg = refined_correct_segment(corrected_seg, poly)
        corrected_segments.append(corrected_seg)
    # Объединяем скорректированные сегменты
    new_coords = []
    for seg in corrected_segments:
        seg_coords = list(seg.coords)
        if new_coords and np.allclose(seg_coords[0], new_coords[-1]):
            new_coords.extend(seg_coords[1:])
        else:
            new_coords.extend(seg_coords)
    return LineString(new_coords)

# Преобразуем сохранённые полигоны в объекты Polygon
polygons = [Polygon(feature['geometry']['coordinates'][0]) for feature in saved_polygons['features']]

# Получаем скорректированный маршрут
corrected_route = refine_route_for_polygons(route_line, polygons)

# --- Отрисовка на карте с Folium ---
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем исходный маршрут (синяя пунктирная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue',
    weight=3,
    opacity=0.7,
    dash_array='5,5'
).add_to(m)

# Отображаем скорректированный маршрут (зелёная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in corrected_route.coords],
    color='orange',
    weight=3,
    opacity=0.8
).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

m

Теперь генерируем точки с шагом в 1м

In [20]:
# Создаем трансформеры: из WGS84 в UTM (например, для Москвы используется EPSG:32637)
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

# Функция для преобразования точки (shapely Point) из UTM обратно в (lat, lng)
def point_to_wgs(pt):
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)

# Преобразуем исходный маршрут в UTM
route_coords_m = [transformer_to_m.transform(lng, lat) for (lng, lat) in route_line.coords]
original_route_m = LineString(route_coords_m)

# Преобразуем corrected_route (в WGS84) в UTM
corrected_coords_m = [transformer_to_m.transform(lng, lat) for (lng, lat) in corrected_route.coords]
corrected_route_m = LineString(corrected_coords_m)

# Функция генерации точек вдоль линии с заданным шагом (в метрах)
def generate_points(line, step):
    points = []
    d = 0.0
    while d <= line.length:
        pt = line.interpolate(d)
        points.append(pt)
        d += step
    return points

step = 1.0  # 1 метр
# Генерируем точки вдоль скорректированного маршрута в UTM
corrected_points_m = generate_points(corrected_route_m, step)

# Разделяем точки: если расстояние до оригинального маршрута (original_route_m) меньше порога,
# считаем, что точка совпадает с исходным маршрутом (safe), иначе – принадлежит обходу (boundary).
tolerance = 1.0  # порог в метрах
safe_points_m = []
boundary_points_m = []

for pt in corrected_points_m:
    if pt.distance(original_route_m) < tolerance:
        safe_points_m.append(pt)
    else:
        boundary_points_m.append(pt)

# Преобразуем обе группы точек обратно в WGS84
safe_points_wgs = [point_to_wgs(pt) for pt in safe_points_m]
boundary_points_wgs = [point_to_wgs(pt) for pt in boundary_points_m]


In [21]:
# Визуализация на карте с Folium
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем исходный маршрут (синяя пунктирная линия)
def to_latlon(coord):
    # coord: (lng, lat)
    return (coord[1], coord[0])


# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)


folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue', weight=3, opacity=0.7, dash_array='5,5'
).add_to(m)

# Отображаем исходный маршрут (синяя пунктирная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue',
    weight=3,
    opacity=0.7,
    dash_array='5,5'
).add_to(m)


# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# # Отображаем скорректированный маршрут (зелёная линия)
# folium.PolyLine(
#     locations=[to_latlon(coord) for coord in corrected_route.coords],
#     color='green', weight=3, opacity=0.8
# ).add_to(m)

# Отображаем safe_points (например, оранжевые кружки)
for pt in safe_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='orange', fill=True, fill_color='orange').add_to(m)

# Отображаем boundary_points (например, фиолетовые кружки)
for pt in boundary_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='purple', fill=True, fill_color='purple').add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

m


### Обработка участков, которые не пересекают полигоны

In [22]:
# Функция для вычисления проекции точки на отрезок с помощью векторной математики
def point_to_segment_projection(point, seg_start, seg_end):
    """
    point, seg_start, seg_end: массивы или кортежи (x, y) в UTM
    Возвращает: (projection, distance)
    projection: координаты проекции (x, y)
    distance: расстояние от точки до проекции
    """
    p = np.array(point)
    a = np.array(seg_start)
    b = np.array(seg_end)
    ab = b - a
    if np.allclose(ab, 0):
        return a, np.linalg.norm(p - a)
    t = np.dot(p - a, ab) / np.dot(ab, ab)
    # Ограничиваем t в интервале [0, 1]
    t = max(0, min(1, t))
    projection = a + t * ab
    distance = np.linalg.norm(p - projection)
    return projection, distance

# Смещает точку, лежащую на границе полигона (poly), наружу на offset_distance метров.
def shift_point_outward(point, poly, offset_distance, delta=0.1):
    """
    point: shapely Point в UTM (точка на границе полигона).
    poly: shapely Polygon в UTM.
    offset_distance: смещение (в метрах).
    delta: небольшое смещение вдоль границы для вычисления касательного вектора.

    Возвращает: новую точку (shapely Point в UTM), смещённую наружу.
    """
    boundary = poly.exterior
    # Находим параметр проекции точки на границу
    t = boundary.project(point)
    # Получаем две близкие точки вдоль границы для вычисления касательного вектора
    try:
        p_prev = boundary.interpolate(t - delta)
        p_next = boundary.interpolate(t + delta)
    except Exception:
        p_prev = point
        p_next = point
    tangent = np.array([p_next.x - p_prev.x, p_next.y - p_prev.y])
    norm = np.linalg.norm(tangent)
    if norm == 0:
        return point
    tangent /= norm
    # Вычисляем правую нормаль: (v_y, -v_x)
    normal = np.array([tangent[1], -tangent[0]])
    # Предварительное смещение
    shifted_coords = np.array([point.x, point.y]) + offset_distance * normal
    shifted_point = Point(shifted_coords)
    # Если смещённая точка оказывается внутри полигона, смещаем в противоположную сторону
    if poly.contains(shifted_point):
        shifted_coords = np.array([point.x, point.y]) - offset_distance * normal
        shifted_point = Point(shifted_coords)
    return shifted_point

# Функция для преобразования полигона (shapely Polygon в WGS84) в UTM
def transform_polygon_to_utm(poly_wgs, transformer):
    # Получаем внешнюю оболочку полигона
    coords = list(poly_wgs.exterior.coords)
    # Если контур не замкнут, добавляем первую точку
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

# Функция для вычисления проекции точки на ближайшую границу среди всех полигонов
def project_point_to_polygons(point_wgs, polygons_utm, transformer_to_m):
    """
    point_wgs: кортеж (lat, lng) – точка в WGS84
    polygons_utm: список объектов Polygon в UTM
    Возвращает: (best_proj, best_dist) где best_proj – проекция точки (в UTM), best_dist – расстояние.
    """
    # Преобразуем точку в UTM; transformer_to_m требует (lon, lat)
    x, y = transformer_to_m.transform(point_wgs[1], point_wgs[0])
    p_utm = np.array([x, y])
    best_proj = None
    best_dist = float('inf')
    for poly in polygons_utm:
        coords = list(poly.exterior.coords)
        # Проходим по каждому ребру полигона
        for i in range(len(coords)-1):
            a = coords[i]
            b = coords[i+1]
            proj, dist = point_to_segment_projection(p_utm, a, b)
            if dist < best_dist:
                best_dist = dist
                best_proj = proj
    return best_proj, best_dist

In [23]:
# Преобразуем сохранённые полигоны в объекты Polygon в UTM
polygons_utm = []
for feature in saved_polygons["features"]:
    poly_wgs = shape(feature["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
    polygons_utm.append(poly_utm)

In [24]:
# Для каждой safe точки (из safe_points_wgs) вычисляем проекцию на ближайшую границу полигона.
projected_safe_points_wgs = []
for pt in safe_points_wgs:
    proj, dist = project_point_to_polygons(pt, polygons_utm, transformer_to_m)
    # Преобразуем проекцию (в UTM) обратно в WGS84
    lng, lat = transformer_to_wgs.transform(proj[0], proj[1])
    projected_safe_points_wgs.append((lat, lng))

In [25]:
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем сохранённые полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем safe_points (оранжевые кружки)
for pt in safe_points_wgs:
    folium.CircleMarker(
        location=pt, radius=3, color='orange', fill=True, fill_color='orange'
    ).add_to(m)

# Отображаем boundary_points (например, фиолетовые кружки)
for pt in boundary_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='purple', fill=True, fill_color='purple').add_to(m)

# Отображаем проекции для safe точек (синие кружки)
# for pt in projected_safe_points_wgs:
#     folium.CircleMarker(
#         location=pt, radius=3, color='blue', fill=True, fill_color='blue'
#     ).add_to(m)

# Соединяем исходные safe точки с их проекциями линией (например, пунктирной)
for orig, proj in zip(safe_points_wgs, projected_safe_points_wgs):
    folium.PolyLine(
        locations=[orig, proj], color='yellow', weight=2, opacity=0.8, dash_array='2,4'
    ).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

m

Обрабатываем массив оранжевых точек с их проекциями (safe_points_wgs, projected_safe_points_wgs) Отмеряем 3 метра от точки сопряжения проекций с гранями полигонов - это будет часть нового маршрута. Добавим логику, которая предотвращает генерацию маршрутных точек внутри полигонов

In [26]:
#-------------------------------
# 2. Трансформеры: WGS84 <-> UTM
# ------------------------------

# Для Москвы часто используют UTM zone 37N (EPSG:32637)
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

def utm_point_to_wgs(pt):
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)


#------------------------------
# 3. Преобразование полигона в UTM (для всех полигонов)
# ------------------------------

def transform_polygon_to_utm(poly_wgs, transformer):
    coords = list(poly_wgs.exterior.coords)
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

from shapely.geometry import shape
polygons_utm = []
for feature in saved_polygons["features"]:
    poly_wgs = shape(feature["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
    polygons_utm.append(poly_utm)


# ------------------------------
# 4. Функция проекции точки на ближайшее ребро среди всех полигонов
# ------------------------------

def point_to_segment_projection(point, seg_start, seg_end):
    p = np.array(point)
    a = np.array(seg_start)
    b = np.array(seg_end)
    ab = b - a
    if np.allclose(ab, 0):
        return a, np.linalg.norm(p - a)
    t = np.dot(p - a, ab) / np.dot(ab, ab)
    t = max(0, min(1, t))
    projection = a + t * ab
    distance = np.linalg.norm(p - projection)
    return projection, distance

def project_point_to_nearest_polygon(point_wgs, polygons_utm, transformer_to_m):
    """
    Для заданной точки в WGS84 находит ближайшую точку на границе среди всех полигонов.
    Возвращает: (best_proj, best_dist, best_poly), где best_proj – координаты проекции (в UTM),
    best_dist – расстояние, best_poly – ближайший полигон.
    """
    x, y = transformer_to_m.transform(point_wgs[1], point_wgs[0])
    p_utm = np.array([x, y])
    best_proj = None
    best_dist = float('inf')
    best_poly = None
    for poly in polygons_utm:
        coords = list(poly.exterior.coords)
        for i in range(len(coords)-1):
            a = coords[i]
            b = coords[i+1]
            proj, dist = point_to_segment_projection(p_utm, a, b)
            if dist < best_dist:
                best_dist = dist
                best_proj = proj
                best_poly = poly
    return best_proj, best_dist, best_poly


# ------------------------------
# 5. Вычисление corrected точек для каждой safe точки
# ------------------------------

# Для каждой safe точки, которая задана в WGS84, находим её проекцию на ближайший полигон.
# Затем вычисляем corrected точку как: corrected = proj + offset_distance * unit_vector,
# где unit_vector = (safe_pt_utm - proj) / ||safe_pt_utm - proj||.
# Если полученная точка оказывается внутри полигона, мы пропускаем эту точку.
offset_distance = 3.0  # смещение в метрах

corrected_projections = []
for pt_wgs in safe_points_wgs:
    # Преобразуем safe точку в UTM
    x_pt, y_pt = transformer_to_m.transform(pt_wgs[1], pt_wgs[0])
    safe_pt_utm = Point(x_pt, y_pt)
    # Находим ближайшую проекцию для этой точки
    best_proj, dist, best_poly = project_point_to_nearest_polygon(pt_wgs, polygons_utm, transformer_to_m)
    if best_proj is None:
        continue
    proj_pt = Point(best_proj)
    v = np.array([safe_pt_utm.x - proj_pt.x, safe_pt_utm.y - proj_pt.y])
    norm_v = np.linalg.norm(v)
    if norm_v == 0:
        candidate = proj_pt
    else:
        unit_v = v / norm_v
        candidate = Point(np.array([proj_pt.x, proj_pt.y]) + offset_distance * unit_v)
    # Если полученная точка candidate внутри ближайшего полигона, пропускаем эту safe точку
    if best_poly.contains(candidate):
        print("Пропускаем точку, candidate внутри полигона.")
        continue
    corrected_projections.append(candidate)

# Преобразуем corrected_projections в WGS84
corrected_points_wgs = []
for cp in corrected_projections:
    lng, lat = transformer_to_wgs.transform(cp.x, cp.y)
    corrected_points_wgs.append((lat, lng))

Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем точку, candidate внутри полигона.
Пропускаем

In [27]:
# ------------------------------
# 6. Визуализация на карте с Folium
# ------------------------------
m = folium.Map(location=[drone_data["lat"], drone_data["lng"]], zoom_start=16)

# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {
        'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3
    }
).add_to(m)

# Маркер дрона
folium.Marker(
    [drone_data["lat"], drone_data["lng"]],
    popup='Дрон', icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Отображаем safe точки (оранжевые кружки)
for pt in safe_points_wgs:
    folium.CircleMarker(
        location=pt, radius=3, color='orange', fill=True, fill_color='orange'
    ).add_to(m)

# # Отображаем проекции (синие кружки)
# projected_safe_points_wgs = []
# for pt in safe_points_wgs:
#     best_proj, dist, _ = project_point_to_nearest_polygon(pt, polygons_utm, transformer_to_m)
#     if best_proj is not None:
#         lng, lat = transformer_to_wgs.transform(best_proj[0], best_proj[1])
#         projected_safe_points_wgs.append((lat, lng))
#         folium.CircleMarker(
#             location=(lat, lng), radius=3, color='blue', fill=True, fill_color='blue'
#         ).add_to(m)

# Отображаем corrected точки (зелёные кружки)
for pt in corrected_points_wgs:
    folium.CircleMarker(
        location=pt, radius=3, color='green', fill=True, fill_color='green'
    ).add_to(m)

# Отображаем boundary_points (например, фиолетовые кружки)
for pt in boundary_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='purple', fill=True, fill_color='purple').add_to(m)

# Соединяем проекции с corrected точками линией (фиолетовая пунктирная)
# for proj_pt, corr_pt in zip(projected_safe_points_wgs, corrected_points_wgs):
#     folium.PolyLine(
#         locations=[proj_pt, corr_pt],
#         color='green', weight=2, opacity=0.8, dash_array='2,4'
#     ).add_to(m)

m

# Алгоритм обработки safe‑точек, НЕ пересекающих полигона

Данный алгоритм позволяет выполнить корректное смещение точек на основе их проекций на границу полигона. В итоге алгоритм генерирует corrected‑точки, расположенные снаружи полигона, что удобно для анализа маршрутов, safe‑точек и других пространственных данных.

---

## 1. Преобразование систем координат (WGS84 ↔ UTM)

- **Входные данные:**
  Данные маршрута, safe‑точек и полигона заданы в системе WGS84 (широта/долгота).

- **Преобразование:**
  Для работы с расстояниями (например, смещение на 3 метра) удобнее использовать метрическую систему, такую как UTM.

- **Трансформация:**
  С помощью трансформеров координаты переводятся из WGS84 в UTM (для Москвы обычно используется зона 37N, EPSG:32637) и обратно.

- **Преимущество:**
  Это позволяет выполнять точные расчёты в метрах.

---

## 2. Преобразование полигона в UTM

- **Преобразование формата:**
  Полигон, сохранённый в формате GeoJSON, преобразуется в объект Shapely.

- **Перевод контура:**
  Затем его внешний контур (boundary) переводится в систему UTM.

- **Назначение:**
  Это нужно для корректной проверки, находится ли точка внутри полигона, а также для правильных расчётов расстояний (например, смещения на 3 м).

---

## 3. Вычисление проекции safe‑точек на границу полигона

- **Исходные данные:**
  Имеется массив safe‑точек (`safe_points_wgs`) и их проекции (`projected_safe_points_wgs`).

- **Процесс вычисления:**
  Для каждой safe‑точки в WGS84:
  - Точка переводится в систему UTM.
  - Для каждого ребра полигона с помощью функции `point_to_segment_projection()` вычисляется проекция точки.
  - Выбирается проекция с минимальным расстоянием до исходной safe‑точки.

- **Результат:**
  Полученные проекции отображаются на карте синими кружками и представляют исходное положение точек на границе полигона.

---

## 4. Смещение проекционных точек (corrected точки)

- **Вычисление вектора смещения:**
  Для каждой пары (safe‑точка, проекция) вычисляется вектор от проекции к safe‑точке, который указывает направление от границы полигона к исходной точке маршрута.

- **Применение смещения:**
  Проекция смещается вдоль этого вектора на фиксированное расстояние (например, `offset_distance` = 3 метра). Результатом является corrected‑точка, которая должна оказаться снаружи полигона.

- **Проверка валидности:**
  Если после смещения полученная точка всё ещё находится внутри полигона, она не включается в итоговый массив.

- **Визуализация:**
  Итоговые corrected‑точки отображаются на карте зелёными кружками.

---

## Ключевой момент алгоритма

**Гарантия корректности:**
Corrected‑точки генерируются на основе проекций, полученных от safe‑точек, и смещаются по направлению от границы полигона к исходной safe‑точке. Это обеспечивает следующее:

- Точки, которые могли бы оказаться внутри полигона, «выбрасываются».
- В итоговом наборе остаются только точки, расположенные снаружи полигона.
- Если после смещения точка остаётся внутри полигона, она пропускается, чтобы исключить ошибочные данные.

---

Этот алгоритм обеспечивает точное смещение safe‑точек, что является важным шагом для анализа маршрутов и пространственных данных в задачах геоинформационных систем.

### Обработка участков, которые пересекают полигоны

In [28]:
import numpy as np
import folium
from shapely.geometry import Point, Polygon, shape
from pyproj import Transformer

# Предполагается, что следующие переменные заданы заранее:
# saved_polygons – GeoJSON с сохранёнными полигонами.
# boundary_points_wgs – либо список точек границы вида [(lat, lng), (lat, lng), ...],
#                        либо список сегментов, где каждый сегмент – список точек [(lat, lng), ...].
# drone_data – словарь с координатами дрона, например: {'lat': ..., 'lng': ...}

# ------------------------------
# 1. Инициализация трансформеров координат
# ------------------------------
# Для Москвы часто используют UTM zone 37N (EPSG:32637)
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

# ------------------------------
# 2. Преобразование точки из UTM в WGS84
# ------------------------------
def utm_point_to_wgs(pt):
    """Преобразует shapely Point из UTM в (lat, lng)"""
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)

# ------------------------------
# 3. Преобразование полигона из WGS84 в UTM
# ------------------------------
def transform_polygon_to_utm(poly_wgs, transformer):
    coords = list(poly_wgs.exterior.coords)
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

if len(saved_polygons["features"]) > 0:
    poly_wgs = shape(saved_polygons["features"][0]["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
else:
    raise ValueError("Нет сохранённых полигонов.")

# ------------------------------
# 4. Преобразование boundary_points_wgs в объекты Point (UTM)
# ------------------------------
# Если передается один сегмент (то есть boundary_points_wgs[0] – кортеж, а не список),
# оборачиваем его в список сегментов.
if boundary_points_wgs and isinstance(boundary_points_wgs[0], (tuple, list)):
    if isinstance(boundary_points_wgs[0][0], (int, float)):
        boundary_points_wgs = [boundary_points_wgs]

segments_utm = []
for segment in boundary_points_wgs:
    seg_utm = []
    for lat, lng in segment:
        x, y = transformer_to_m.transform(lng, lat)
        seg_utm.append(Point(x, y))
    segments_utm.append(seg_utm)

# ------------------------------
# 5. Функции для смещения точек
# ------------------------------
def is_valid(pt, poly):
    """Точка валидна, если не содержится в полигоне и не касается его границы."""
    return (not poly.contains(pt)) and (not poly.touches(pt))

def shift_by_neighbor(point, idx, points, poly, base_offset):
    """
    Для внутренних точек вычисляет смещение по биссектрисе угла, образованного
    векторами к предыдущему и следующему соседу (граница считается замкнутой).
    Если один из кандидатов валиден (находится вне полигона), возвращает его, иначе None.
    """
    n = len(points)
    if n < 2:
        return point

    neighbor_prev = points[(idx - 1) % n]
    neighbor_next = points[(idx + 1) % n]

    v1 = np.array([neighbor_next.x - point.x, neighbor_next.y - point.y])
    v2 = np.array([point.x - neighbor_prev.x, point.y - neighbor_prev.y])

    norm1 = np.linalg.norm(v1)
    norm2 = np.linalg.norm(v2)
    if norm1 == 0 or norm2 == 0:
        return point

    v1_unit = v1 / norm1
    v2_unit = v2 / norm2
    bisector = v1_unit + v2_unit
    norm_bis = np.linalg.norm(bisector)
    if norm_bis == 0:
        bisector = np.array([-v1_unit[1], v1_unit[0]])
    else:
        bisector = bisector / norm_bis

    perp1 = np.array([-bisector[1], bisector[0]])
    perp2 = np.array([bisector[1], -bisector[0]])

    candidate1 = Point(point.x + base_offset * perp1[0],
                       point.y + base_offset * perp1[1])
    candidate2 = Point(point.x + base_offset * perp2[0],
                       point.y + base_offset * perp2[1])

    if is_valid(candidate1, poly):
        return candidate1
    elif is_valid(candidate2, poly):
        return candidate2
    else:
        return None

# Базовое смещение (в метрах)
base_offset = 3.0
# Вычисляем offset-полигон для fallback-проекции
poly_offset = poly_utm.buffer(base_offset, resolution=16, join_style=2, cap_style=2)

def shift_point(point, idx, points, poly, base_offset, poly_offset):
    """
    Пытается сместить точку методом shift_by_neighbor.
    Если кандидат невалиден, выполняется fallback-проекция на внешний контур offset-полигона.
    """
    candidate = shift_by_neighbor(point, idx, points, poly, base_offset)
    if candidate is None or not is_valid(candidate, poly):
        t = poly_offset.exterior.project(point)
        candidate = poly_offset.exterior.interpolate(t)
        if not is_valid(candidate, poly):
            candidate = Point(candidate.x + 0.1, candidate.y + 0.1)
    return candidate

# ------------------------------
# 6. Смещение всех точек каждого сегмента
# ------------------------------
shifted_segments_utm = []
for segment in segments_utm:
    shifted_segment = []
    n = len(segment)
    for i, pt in enumerate(segment):
        if i == n - 1 and n > 1:
            # Для крайней точки сегмента попробуем использовать усреднение векторов смещения
            # для нескольких предыдущих точек (если их достаточно), чтобы получить более стабильный угол.
            k = min(3, n - 1)  # используем до 3 последних смещённых точек, если есть
            disp_vectors = []
            # Если k=0, то просто fallback
            if k > 0:
                for j in range(n - 1 - k, n - 1):
                    dx = shifted_segment[j].x - segment[j].x
                    dy = shifted_segment[j].y - segment[j].y
                    disp_vectors.append((dx, dy))
                avg_disp = np.mean(disp_vectors, axis=0)
                candidate = Point(pt.x + avg_disp[0], pt.y + avg_disp[1])
            else:
                candidate = shift_point(pt, i, segment, poly_utm, base_offset, poly_offset)
            # Если кандидат по усреднённому вектору недопустим, пробуем fallback:
            if not is_valid(candidate, poly_utm):
                # Попытка по локальной касательной крайнего отрезка
                tangent = np.array([segment[i].x - segment[i-1].x, segment[i].y - segment[i-1].y])
                norm_t = np.linalg.norm(tangent)
                if norm_t != 0:
                    t_unit = tangent / norm_t
                    normal1 = np.array([-t_unit[1], t_unit[0]])
                    normal2 = np.array([t_unit[1], -t_unit[0]])
                    candidate1 = Point(pt.x + base_offset * normal1[0], pt.y + base_offset * normal1[1])
                    candidate2 = Point(pt.x + base_offset * normal2[0], pt.y + base_offset * normal2[1])
                    if is_valid(candidate1, poly_utm):
                        candidate = candidate1
                    elif is_valid(candidate2, poly_utm):
                        candidate = candidate2
                    else:
                        t_proj = poly_offset.exterior.project(pt)
                        candidate = poly_offset.exterior.interpolate(t_proj)
                        if not is_valid(candidate, poly_utm):
                            candidate = Point(candidate.x + 0.1, candidate.y + 0.1)
                else:
                    candidate = shift_point(pt, i, segment, poly_utm, base_offset, poly_offset)
        else:
            candidate = shift_point(pt, i, segment, poly_utm, base_offset, poly_offset)
        shifted_segment.append(candidate)
    shifted_segments_utm.append(shifted_segment)

# ------------------------------
# 7. Преобразование точек обратно в WGS84
# ------------------------------
segments_wgs = []
shifted_segments_wgs = []
for segment in segments_utm:
    seg_wgs = [utm_point_to_wgs(pt) for pt in segment]
    segments_wgs.append(seg_wgs)
for segment in shifted_segments_utm:
    seg_wgs = [utm_point_to_wgs(pt) for pt in segment]
    shifted_segments_wgs.append(seg_wgs)

# ------------------------------
# 8. Визуализация на карте с Folium
# ------------------------------
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=16)

folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Исходные точки (синие)
for seg in segments_wgs:
    for pt in seg:
        folium.CircleMarker(location=pt, radius=3, color='blue', fill=True, fill_color='blue').add_to(m)

# Смещённые точки (красные)
for seg in shifted_segments_wgs:
    for pt in seg:
        folium.CircleMarker(location=pt, radius=3, color='red', fill=True, fill_color='red').add_to(m)

# Соединяем исходные точки с соответствующими смещёнными (фиолетовая пунктирная линия)
for seg_orig, seg_shift in zip(segments_wgs, shifted_segments_wgs):
    for orig, shifted in zip(seg_orig, seg_shift):
        folium.PolyLine(locations=[orig, shifted], color='purple', weight=2, opacity=0.8, dash_array='2,4').add_to(m)

folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='black', icon='info-sign')
).add_to(m)

m

# Алгоритм смещения точек, пересекающих границы полигона

Данный алгоритм предназначен для корректного смещения точек границы полигона наружу на заданное расстояние, с сохранением устойчивости углов смещения между точками. Результат визуализируется с помощью Folium, где исходные точки обозначаются синими, а смещённые — красными.

---

## 1. Расчёт смещения для внутренних точек

### Метод биссектрисы

Для точек, не являющихся крайними в сегменте, направление смещения определяется следующим образом:

- **Выбор соседних точек:**
  Выбираются две соседние точки — предыдущая и следующая. При этом используется циклическое индексирование, т.е. граница считается замкнутой.

- **Вычисление векторов:**
  Рассчитываются векторы от текущей точки к выбранным соседям.

- **Нормализация и суммирование:**
  Нормализованные векторы суммируются. Полученная сумма (после нормализации) задаёт направление биссектрисы угла, образованного соседними векторами.

- **Вычисление нормалей:**
  Затем от полученного вектора биссектрисы вычисляются два перпендикулярных направления (нормали), повёрнутых на 90°.

- **Выбор валидного кандидата:**
  Из двух кандидатов выбирается тот, который является «валидным», т.е. смещённая точка не попадает внутрь полигона и не касается его границы.

Таким образом, смещение происходит наружу, и для внутренних точек результат получается достаточно устойчивым.

---

## 2. Расчёт смещения для крайних (последних) точек каждого сегмента

Для крайних точек применяется иной подход, так как прямой расчёт биссектрисы может дать некорректный угол.

### Усреднение предыдущих смещений

- **Вычисление векторов смещения:**
  Для последней точки сегмента алгоритм пытается вычислить вектор смещения на основе уже полученных смещённых точек для предыдущих (до трёх) точек сегмента.

  - Для каждой из последних точек (кроме самой крайней) вычисляется вектор смещения как разница между смещённой точкой и исходной.

- **Усреднение векторов:**
  Затем берётся среднее этих векторов, что позволяет получить усреднённый вектор, близкий по направлению к тому, как смещаются остальные точки.

- **Применение усреднённого вектора:**
  Усреднённый вектор прибавляется к координатам крайней точки, чтобы получить кандидата на смещение. Это сохраняет согласованность направления с предыдущими точками.

### Fallback через локальную касательную

Если кандидат, полученный по усреднённому вектору, оказывается недопустимым (например, попадает внутрь полигона):

- **Вычисление локального вектора:**
  Рассчитывается вектор последнего отрезка (от предпоследней к последней исходной точке).

- **Нахождение нормалей:**
  Для этого вектора вычисляются две нормали (поворот на 90° в обе стороны).

- **Выбор валидного кандидата:**
  Из полученных кандидатов выбирается тот, который удовлетворяет условию валидности.

Таким образом, даже если усреднение дает неправильное направление, fallback гарантирует, что крайняя точка смещается строго под углом 90° к границе, определяемой последним отрезком.

---

## 3. Проверка валидности смещённых точек

Для каждой сгенерированной смещённой точки вызывается функция `is_valid`, которая проверяет, что точка:
- Не попадает внутрь исходного полигона.
- Не касается границы полигона.

Если кандидат не проходит проверку, применяется fallback‑метод: точка проецируется на внешний контур offset‑полигона с небольшим дополнительным смещением.

---

## 4. Преобразование результатов и визуализация

После смещения точек в системе UTM:

- **Преобразование координат:**
  Все точки преобразуются обратно в систему WGS84 для дальнейшей визуализации.

- **Визуализация с использованием Folium:**
  - **Исходные точки** отображаются синими метками.
  - **Смещённые точки** отображаются красными метками.
  - Каждая исходная точка соединяется с соответствующей смещённой точкой пунктирной (фиолетовой) линией.
  - На карте также присутствует маркер дрона, отображаемый в виде черного значка.

---

Этот алгоритм обеспечивает согласованное и устойчивое смещение точек границы полигона наружу, с сохранением правильного угла смещения как для внутренних, так и для крайних точек сегментов.

## Объединение скорректированных точек в финальный маршрут и обработка

In [29]:
# ------------------------------------------
# Функции для построения маршрута
# ------------------------------------------

def distance(pt1, pt2):
    """
    Простое евклидово расстояние в радианах (lat/lng),
    НЕ учитывает кривизну Земли. Для больших дистанций
    лучше использовать geopy.distance или UTM.
    """
    lat1, lng1 = pt1
    lat2, lng2 = pt2
    rlat1, rlng1 = math.radians(lat1), math.radians(lng1)
    rlat2, rlng2 = math.radians(lat2), math.radians(lng2)
    dlat = rlat2 - rlat1
    dlng = rlng2 - rlng1
    return math.sqrt(dlat*dlat + dlng*dlng)

def build_route_explicit_start(start_point, all_points):
    """
    Жадный алгоритм, начиная НЕ от дрона, а от заданной 'start_point'.
    1) Помещаем start_point в маршрут
    2) На каждом шаге ищем ближайшую точку из непосещённых
    3) Идём к ней, удаляем из списка, повторяем
    """
    # Скопируем список всех точек, чтобы не менять исходник
    points_to_visit = all_points.copy()

    # Убираем start_point из списка, если она там есть
    if start_point in points_to_visit:
        points_to_visit.remove(start_point)

    route = [start_point]      # Маршрут начинается с заданной точки
    current_point = start_point

    # Пока остались непосещённые точки
    while points_to_visit:
        nearest_pt = min(points_to_visit, key=lambda p: distance(current_point, p))
        route.append(nearest_pt)
        points_to_visit.remove(nearest_pt)
        current_point = nearest_pt

    return route


# def build_route_with_drone_first(drone_data, first_point, all_points):
#     """
#     Сначала маршрут от дрона к 'first_point',
#     а дальше - обычный nearest neighbor по оставшимся точкам.
#     """
#     # Стартуем с дрона
#     drone_coord = (drone_data['lat'], drone_data['lng'])
#     route = [drone_coord]
#
#     # 1) Сразу добавляем first_point вторым шагом
#     route.append(first_point)
#
#     # 2) Убираем first_point из списка, если есть
#     points_to_visit = all_points.copy()
#     if first_point in points_to_visit:
#         points_to_visit.remove(first_point)
#
#     current_point = first_point
#
#     while points_to_visit:
#         nearest_pt = min(points_to_visit, key=lambda p: distance(current_point, p))
#         route.append(nearest_pt)
#         points_to_visit.remove(nearest_pt)
#         current_point = nearest_pt
#
#     return route


1.	build_route_explicit_start(start_point, all_points)

	•	Маршрут сразу начинается с start_point.

	•	Это означает, что координаты дрона не участвуют как «точка старта». Мы как бы говорим: «Вот моя первая точка, с неё начинаем обход, а дальше — по ближайшим».

	•	Результирующий маршрут выглядит примерно так:

	start_point -> ближайшая_точка -> ... -> последняя_точка

2. build_route_with_drone_first(drone_data, first_point, all_points)

	•	Маршрут начинается с координат дрона.
	•	Затем мы «насильно» идём к first_point, и только после этого идём по ближайшим непосещённым точкам.
	•	Результирующий маршрут выглядит так:

    drone_position -> first_point -> ближайшая_точка -> ... -> последняя_точка


In [30]:
# ------------------------------------------
# 1. Собираем все точки в один список
# ------------------------------------------
all_points = list(corrected_points_wgs)
for seg in shifted_segments_wgs:
    all_points.extend(seg)

# ------------------------------------------
# 2. Строим финальный маршрут
# ------------------------------------------
# 1) Собираем все точки в один список
all_points = list(corrected_points_wgs)
for seg in shifted_segments_wgs:
    all_points.extend(seg)

# 2) Явно выбираем, какая точка будет первой
first_pt = corrected_points_wgs[0]

# 3) Если хотим стартовать сразу с этой точки (и не учитывать дрона)
final_route = build_route_explicit_start(first_pt, all_points)

# ЛИБО, если хотим, чтобы дрон сперва летел к этой точке:
# final_route = build_route_with_drone_first(drone_data, first_pt, all_points)

In [31]:
# 1) Создаем базовую карту
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=16)

# 2) Полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {
        'fillColor': 'gray',
        'color': 'black',
        'weight': 2,
        'fillOpacity': 0.3
    }
).add_to(m)

# 3) Маркер дрона
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# 4) Готовим TimestampedGeoJson данные
start_time = datetime(2025, 3, 22, 12, 0, 0)   # произвольная отправная дата/время
time_step = timedelta(seconds=2)              # шаг 2 сек на каждый "кадр"
current_time = start_time

features = []

# Определяем максимальную длину двух списков,
# чтобы пройтись в одном цикле.
max_len = max(len(safe_points_wgs), len(final_route))

for i in range(max_len):
    # Если в safe_points_wgs ещё есть точка с индексом i
    if i < len(safe_points_wgs):
        lat, lng = safe_points_wgs[i]
        feature = {
            "type": "Feature",
            "geometry": {
                "type": "Point",
                "coordinates": [lng, lat]  # (lng, lat) для GeoJSON
            },
            "properties": {
                "time": current_time.isoformat(),  # та же метка времени для safe + route
                "style": {
                    "color": "orange",
                    "fillColor": "orange",
                    "radius": 5
                },
                "icon": "circle",
                "popup": f"Safe point #{i+1}"
            }
        }
        features.append(feature)

    # Если в final_route ещё есть точка с индексом i
    if i < len(final_route):
        lat, lng = final_route[i]
        feature = {
            "type": "Feature",
            "geometry": {
                "type": "Point",
                "coordinates": [lng, lat]
            },
            "properties": {
                "time": current_time.isoformat(),
                "style": {
                    "color": "blue",
                    "fillColor": "blue",
                    "radius": 5
                },
                "icon": "circle",
                "popup": f"Route point #{i+1}"
            }
        }
        features.append(feature)

    # Переходим к следующему моменту времени (следующий «кадр»)
    current_time += time_step

# Объединяем все фичи в FeatureCollection
data = {
    "type": "FeatureCollection",
    "features": features
}

# 5) Создаём TimestampedGeoJson слой
TimestampedGeoJson(
    data,
    transition_time=200,  # длительность перехода (мс) между соседними "кадрами"
    loop=False,
    auto_play=False,
    add_last_point=True,
    period='PT1S'
).add_to(m)

# 6) Отображаем карту в Jupyter
m

Чистим маршрут от очень близко расположенных точек

In [32]:
def reduce_route(route, min_distance_m=0.9):
    """
    Удаляет «лишние» точки, которые ближе, чем min_distance_m (в метрах)
    к предыдущей сохранённой точке.

    Аргументы:
        route (list of (lat, lng)): исходный маршрут
        min_distance_m (float): минимально допустимая дистанция между соседними точками

    Возвращает:
        list of (lat, lng): "разреженный" маршрут
    """
    if not route:
        return []

    reduced = [route[0]]  # начинаем с первой точки

    for pt in route[1:]:
        last_pt = reduced[-1]

        # Вычисляем расстояние (в метрах) между последней сохранённой точкой и текущей
        dist_m = geodesic(last_pt, pt).meters

        if dist_m >= min_distance_m:
            # Только если точка дальше чем min_distance_m, добавляем её
            reduced.append(pt)
        # иначе просто пропускаем pt, не добавляя в reduced

    return reduced

In [33]:
# Пример: убираем точки, которые ближе 0.9 м друг к другу
cleaned_route = reduce_route(final_route, min_distance_m=0.9)

In [34]:
# 1) Создаем базовую карту
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=16)

# 2) Полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {
        'fillColor': 'gray',
        'color': 'black',
        'weight': 2,
        'fillOpacity': 0.3
    }
).add_to(m)

# 3) Маркер дрона
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# 4) Готовим TimestampedGeoJson данные
start_time = datetime(2025, 3, 22, 12, 0, 0)   # произвольная отправная дата/время
time_step = timedelta(seconds=2)              # шаг 2 сек на каждый "кадр"
current_time = start_time

features = []

# Определяем максимальную длину двух списков,
# чтобы пройтись в одном цикле.
max_len = max(len(safe_points_wgs), len(cleaned_route))

for i in range(max_len):
    # Если в safe_points_wgs ещё есть точка с индексом i
    if i < len(safe_points_wgs):
        lat, lng = safe_points_wgs[i]
        feature = {
            "type": "Feature",
            "geometry": {
                "type": "Point",
                "coordinates": [lng, lat]  # (lng, lat) для GeoJSON
            },
            "properties": {
                "time": current_time.isoformat(),  # та же метка времени для safe + route
                "style": {
                    "color": "orange",
                    "fillColor": "orange",
                    "radius": 5
                },
                "icon": "circle",
                "popup": f"Safe point #{i+1}"
            }
        }
        features.append(feature)

    # Если в cleaned_route ещё есть точка с индексом i
    if i < len(cleaned_route):
        lat, lng = cleaned_route[i]
        feature = {
            "type": "Feature",
            "geometry": {
                "type": "Point",
                "coordinates": [lng, lat]
            },
            "properties": {
                "time": current_time.isoformat(),
                "style": {
                    "color": "blue",
                    "fillColor": "blue",
                    "radius": 5
                },
                "icon": "circle",
                "popup": f"Route point #{i+1}"
            }
        }
        features.append(feature)

    # Переходим к следующему моменту времени (следующий «кадр»)
    current_time += time_step

# Объединяем все фичи в FeatureCollection
data = {
    "type": "FeatureCollection",
    "features": features
}

# 5) Создаём TimestampedGeoJson слой
TimestampedGeoJson(
    data,
    transition_time=200,  # длительность перехода (мс) между соседними "кадрами"
    loop=False,
    auto_play=False,
    add_last_point=True,
    period='PT1S'
).add_to(m)

# 6) Отображаем карту в Jupyter
m

In [35]:
print(len(final_route))
print(len(cleaned_route))

791
628
